## ALBERT PIPELINE

In [1]:
# Imports
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
!pip install simpletransformers
from simpletransformers.classification import ClassificationModel, ClassificationArgs
from sklearn.model_selection import KFold
from sklearn.metrics import accuracy_score
from sklearn.metrics import precision_recall_fscore_support
from sklearn.metrics import f1_score, recall_score, precision_score
from sklearn.metrics import matthews_corrcoef

# Check GPU
gpu_info = !nvidia-smi
gpu_info = '\n'.join(gpu_info)
if gpu_info.find('failed') >= 0:
  print('Not connected to a GPU')
else:
  print(gpu_info)

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     |████████████████████████████████| 250 kB 4.9 MB/s 
     |████████████████████████████████| 9.2 MB 76.4 MB/s 
     |████████████████████████████████| 43 kB 2.2 MB/s 
     |████████████████████████████████| 7.6 MB 63.4 MB/s 
     |████████████████████████████████| 1.3 MB 74.3 MB/s 
     |████████████████████████████████| 441 kB 75.9 MB/s 
     |████████████████████████████████| 1.9 MB 65.4 MB/s 
     |████████████████████████████████| 5.5 MB 66.7 MB/s 
     |████████████████████████████████| 163 kB 78.1 MB/s 
     |████████████████████████████████| 182 kB 75.4 MB/s 
     |████████████████████████████████| 166 kB 74.0 MB/s 
     |████████████████████████████████| 63 kB 1.9 MB/s 
     |████████████████████████████████| 166 kB 79.9 MB/s 
     |████████████████████████████████| 162 kB 78.7 MB/s 
     |████████████████████████████████| 162 kB 81.9 MB/s 
     |██████████████████████████████

In [2]:
# Load the dataset from google drive
from google.colab import drive
drive.mount('/content/drive')

# Import downsampled dataset
df = pd.read_excel('/content/drive/MyDrive/KANO Modell Studie/Datasets/LabeledDatasets/DATASET_downsampled.xlsx')

# Import without google drive
# df = pd.read_excel('DATASET_downsampled.xlsx')

df = df.drop(columns = ['Unnamed: 0'])

df.info()

Mounted at /content/drive
<class 'pandas.core.frame.DataFrame'>
RangeIndex: 2592 entries, 0 to 2591
Data columns (total 3 columns):
 #   Column       Non-Null Count  Dtype 
---  ------       --------------  ----- 
 0   review       2592 non-null   object
 1   kano_labels  2592 non-null   object
 2   labels       2592 non-null   int64 
dtypes: int64(1), object(2)
memory usage: 60.9+ KB


In [3]:
# Show the distribution of the labels
print(df['labels'].value_counts())

0    648
2    648
3    648
1    648
Name: labels, dtype: int64


In [4]:
# Rename the columns so that simple transformers can handle them
train_data = df[['review','labels']]
train_data.columns = ['text', 'labels']
train_data.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 2592 entries, 0 to 2591
Data columns (total 2 columns):
 #   Column  Non-Null Count  Dtype 
---  ------  --------------  ----- 
 0   text    2592 non-null   object
 1   labels  2592 non-null   int64 
dtypes: int64(1), object(1)
memory usage: 40.6+ KB


In [5]:
# Model implementation and k-fold cross validation with Simpletransformers

# Wrapper function to calculate f1-score with additional parameters
def f1_multiclass(labels, preds):
    return f1_score(labels, preds, average = None)

# Wrapper function to calculate recall with additional parameters
def recall_multiclass(labels, preds):
    return recall_score(labels, preds, average = None)

# Wrapper function to calculate precision with additional parameters
def precision_multiclass(labels, preds):
    return precision_score(labels, preds, average = None)

# K-fold cross validation with 10 folds
n = 10
kf = KFold(n_splits=n, random_state = 42, shuffle = True)

# Lists to store the values of accuracy, f1-score, precision and recall for all 10 folds
resultsAcc = []
resultsf1 = []
resultsPrecision = []
resultsRecall = []

model_args = ClassificationArgs(
    num_train_epochs=1, 
    use_multiprocessing=False,
    use_multiprocessing_for_evaluation=False,
    overwrite_output_dir= True
)

# Create the ClassificationModel
model = ClassificationModel(
    'albert',
    'albert-base-v2',
    num_labels=4,
    args=model_args,
    #use_cuda=False
) 

for train_index, val_index in kf.split(train_data):
  train_df = train_data.iloc[train_index]
  val_df = train_data.iloc[val_index]

  model.train_model(train_df)
  result, model_outputs, wrong_predictions = model.eval_model(val_df, f1=f1_multiclass, acc=accuracy_score, recall=recall_multiclass, precision=precision_multiclass)
  print(result)
  
  # Add scores to the respective lists
  resultsAcc.append(result['acc'])
  resultsf1.append(result['f1'])
  resultsPrecision.append(result['precision'])
  resultsRecall.append(result['recall'])

  print("results accuracy",resultsAcc)
  print(f"Mean-Precision: {sum(resultsAcc) / len(resultsAcc)}")
  print('results f1: ', resultsf1)
  print('results precision: ', resultsPrecision)
  print('results recall: ', resultsRecall)

Downloading:   0%|          | 0.00/684 [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/47.4M [00:00<?, ?B/s]

Some weights of the model checkpoint at albert-base-v2 were not used when initializing AlbertForSequenceClassification: ['predictions.decoder.weight', 'predictions.dense.weight', 'predictions.bias', 'predictions.decoder.bias', 'predictions.LayerNorm.bias', 'predictions.LayerNorm.weight', 'predictions.dense.bias']
- This IS expected if you are initializing AlbertForSequenceClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing AlbertForSequenceClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of AlbertForSequenceClassification were not initialized from the model checkpoint at albert-base-v2 and are newly initialized: ['classifier.weight', 'classifier.bias']
You sho

Downloading:   0%|          | 0.00/760k [00:00<?, ?B/s]

Epoch:   0%|          | 0/1 [00:00<?, ?it/s]

...

{'mcc': 0.9279596287053297, 'f1': array([0.97810219, 0.93457944, 0.95238095, 0.91338583]), 'acc': 0.9459459459459459, 'recall': array([0.95714286, 0.96153846, 0.97222222, 0.89230769]), 'precision': array([1.        , 0.90909091, 0.93333333, 0.93548387]), 'eval_loss': 0.26745373131107597}
results accuracy [0.75, 0.7576923076923077, 0.7606177606177607, 0.806949806949807, 0.8957528957528957, 0.8687258687258688, 0.9034749034749034, 0.9227799227799228, 0.9459459459459459]
Mean-Precision: 0.8457710457710457
results f1:  [array([0.85496183, 0.7027027 , 0.86206897, 0.592     ]), array([0.85074627, 0.74242424, 0.85517241, 0.53211009]), array([0.90076336, 0.69064748, 0.85483871, 0.59677419]), array([0.89430894, 0.77165354, 0.86153846, 0.71014493]), array([0.95522388, 0.89361702, 0.88288288, 0.84848485]), array([0.95      , 0.84057971, 0.88235294, 0.80645161]), array([0.96551724, 0.87218045, 0.92307692, 0.84552846]), array([0.94214876, 0.91071429, 0.94520548, 0.89208633]), array([0.97810219, 0.93

Epoch:   0%|          | 0/1 [00:00<?, ?it/s]

Running Epoch 0 of 1:   0%|          | 0/292 [00:00<?, ?it/s]

Running Evaluation:   0%|          | 0/33 [00:00<?, ?it/s]

{'mcc': 0.9485664556786775, 'f1': array([0.94964029, 0.9924812 , 0.96491228, 0.93939394]), 'acc': 0.9613899613899614, 'recall': array([0.97058824, 0.98507463, 0.94827586, 0.93939394]), 'precision': array([0.92957746, 1.        , 0.98214286, 0.93939394]), 'eval_loss': 0.19239372556859796}
results accuracy [0.75, 0.7576923076923077, 0.7606177606177607, 0.806949806949807, 0.8957528957528957, 0.8687258687258688, 0.9034749034749034, 0.9227799227799228, 0.9459459459459459, 0.9613899613899614]
Mean-Precision: 0.8573329373329373
results f1:  [array([0.85496183, 0.7027027 , 0.86206897, 0.592     ]), array([0.85074627, 0.74242424, 0.85517241, 0.53211009]), array([0.90076336, 0.69064748, 0.85483871, 0.59677419]), array([0.89430894, 0.77165354, 0.86153846, 0.71014493]), array([0.95522388, 0.89361702, 0.88288288, 0.84848485]), array([0.95      , 0.84057971, 0.88235294, 0.80645161]), array([0.96551724, 0.87218045, 0.92307692, 0.84552846]), array([0.94214876, 0.91071429, 0.94520548, 0.89208633]), arr

In [6]:
print("results accuracy",resultsAcc)
print('results f1: ', resultsf1)
print('results precision: ', resultsPrecision)
print('results recall: ', resultsRecall)

results accuracy [0.75, 0.7576923076923077, 0.7606177606177607, 0.806949806949807, 0.8957528957528957, 0.8687258687258688, 0.9034749034749034, 0.9227799227799228, 0.9459459459459459, 0.9613899613899614]
results f1:  [array([0.85496183, 0.7027027 , 0.86206897, 0.592     ]), array([0.85074627, 0.74242424, 0.85517241, 0.53211009]), array([0.90076336, 0.69064748, 0.85483871, 0.59677419]), array([0.89430894, 0.77165354, 0.86153846, 0.71014493]), array([0.95522388, 0.89361702, 0.88288288, 0.84848485]), array([0.95      , 0.84057971, 0.88235294, 0.80645161]), array([0.96551724, 0.87218045, 0.92307692, 0.84552846]), array([0.94214876, 0.91071429, 0.94520548, 0.89208633]), array([0.97810219, 0.93457944, 0.95238095, 0.91338583]), array([0.94964029, 0.9924812 , 0.96491228, 0.93939394])]
results precision:  [array([0.875     , 0.64197531, 0.92592593, 0.60655738]), array([0.79166667, 0.73134328, 0.84931507, 0.60416667]), array([0.83098592, 0.64864865, 0.88333333, 0.68518519]), array([0.87301587, 0.

In [7]:
# Calculate the average precision, recall and f1-scores of the 10 folds for each label

def PrecisionRecallF1Table(resultsPrecision, resultsRecall, resultsf1):

  np_resultsPrecision = np.array(resultsPrecision)
  np_resultsRecall = np.array(resultsRecall)
  np_resultsf1  = np.array(resultsf1)

  # Calculate the mean precision for each label
  df_resultsPrecision = pd.DataFrame(np_resultsPrecision, columns=list('BDIP'))
  precision_b_mean = df_resultsPrecision['B'].mean()
  precision_d_mean = df_resultsPrecision['D'].mean()
  precision_i_mean = df_resultsPrecision['I'].mean()
  precision_p_mean = df_resultsPrecision['P'].mean()

  # Calculate the mean recall for each label
  df_resultsRecall = pd.DataFrame(np_resultsRecall, columns=list('BDIP'))
  recall_b_mean = df_resultsRecall['B'].mean()
  recall_d_mean = df_resultsRecall['D'].mean()
  recall_i_mean = df_resultsRecall['I'].mean()
  recall_p_mean = df_resultsRecall['P'].mean()

  # Calculate the mean f1-score for each label
  df_resultsf1 = pd.DataFrame(np_resultsf1, columns=list('BDIP'))
  f1_b_mean = df_resultsf1['B'].mean()
  f1_d_mean = df_resultsf1['D'].mean()
  f1_i_mean = df_resultsf1['I'].mean()
  f1_p_mean = df_resultsf1['P'].mean()

  # Create dataframe with summarized results
  metrics = [{'B': precision_b_mean, 'D': precision_d_mean, 'I': precision_i_mean, 'P':precision_p_mean},
          {'B': recall_b_mean, 'D': recall_d_mean, 'I': recall_i_mean, 'P': recall_p_mean},
          {'B': f1_b_mean, 'D': f1_d_mean, 'I': f1_i_mean, 'P': f1_p_mean} ]
  train_df_metrics = pd.DataFrame(metrics, index=['Average precision',
                                'Average recall',
                                'Average F1-Score'])
  return train_df_metrics

PrecisionRecallF1Table(resultsPrecision, resultsRecall, resultsf1)

B         D         I         P
Average precision  0.913309  0.830695  0.906965  0.779782
Average recall     0.937861  0.842014  0.891171  0.759666
Average F1-Score   0.924141  0.835158  0.898443  0.767636

## Training on the dataset at hand, testing on the 'Trainingskorpus' dataset

In [8]:
# Import of 'Trainingskorpus_Final', which gives the final labeling
testset1 = pd.read_excel('/content/drive/MyDrive/KANO Modell Studie/Datasets/LabeledDatasets/Trainingskorpus_Final.xlsx')

# Import without google drive
# testset1 = pd.read_excel('Trainingskorpus_Final.xlsx')

testset1 = testset1.drop(columns = ['Unnamed: 0'])
testset1.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1622 entries, 0 to 1621
Data columns (total 2 columns):
 #   Column       Non-Null Count  Dtype 
---  ------       --------------  ----- 
 0   review       1622 non-null   object
 1   kano_labels  1622 non-null   object
dtypes: object(2)
memory usage: 25.5+ KB


In [9]:
# Show the distribution of the labels
print(testset1['kano_labels'].value_counts())

B    1102
P     395
D      95
I      30
Name: kano_labels, dtype: int64


In [10]:
# Import of 'Trainingskorpus_InitialLabels', which gives the initial labeling of two sometimes differing labels
testset2 = pd.read_excel('/content/drive/MyDrive/KANO Modell Studie/Datasets/LabeledDatasets/Trainingskorpus_InitialLabels.xlsx')

# Import without google drive
# testset2 = pd.read_excel('Trainingskorpus_InitialLabels.xlsx')

testset2 = testset2.drop(columns = ['Unnamed: 0'])
testset2.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1622 entries, 0 to 1621
Data columns (total 3 columns):
 #   Column   Non-Null Count  Dtype 
---  ------   --------------  ----- 
 0   review   1622 non-null   object
 1   label 1  1622 non-null   object
 2   label 2  1622 non-null   object
dtypes: object(3)
memory usage: 38.1+ KB


In [11]:
# Merge the two sets so we have the final labels as well as the initial labels in the testset
testset = testset1.merge(testset2, left_on='review', right_on='review')
testset.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 1622 entries, 0 to 1621
Data columns (total 4 columns):
 #   Column       Non-Null Count  Dtype 
---  ------       --------------  ----- 
 0   review       1622 non-null   object
 1   kano_labels  1622 non-null   object
 2   label 1      1622 non-null   object
 3   label 2      1622 non-null   object
dtypes: object(4)
memory usage: 63.4+ KB


In [12]:
# Add a column 'equal' which is True if the two initial labels are equal and false otherwise

equal = [None]*np.size(testset['review'])

i = 0
for label1, label2 in zip(testset2['label 1'], testset2['label 2']):
  if(label1 == label2):
    equal[i] = True
  else:
    equal[i] = False
  i += 1
  
testset['equal'] = equal

In [13]:
# Calculate the accuracy of the whole testset as well as 
# only the parts where the inital two labels are equal (accuracy_clear)
# or differ (accuracy_diff)

accuracy_clear = 0.
accuracy_diff = 0.
n_clear = 0
n_diff = 0
all_predicted_labels = []
predicted_labels_equal_initial_label = []
predicted_labels_diff_initial_label = []
true_label_equal = []
true_label_diff = []

for label, review, equal in zip(testset['kano_labels'],  testset['review'], testset['equal']):
  
  test_prediction, raw_outputs = model.predict([review])
  
  predicted_label = ''

  if test_prediction[0] == 0:
    predicted_label = 'B'
  if test_prediction[0] == 1:
    predicted_label = 'D'
  if test_prediction[0] == 2:
    predicted_label = 'I'
  if test_prediction[0] == 3:
    predicted_label = 'P'

  all_predicted_labels.append(predicted_label)
  
  if equal:
    n_clear += 1
    predicted_labels_equal_initial_label.append(predicted_label)
    true_label_equal.append(label)
    if label == predicted_label:
      accuracy_clear += 1.

  if not equal:
    n_diff += 1
    predicted_labels_diff_initial_label.append(predicted_label)
    true_label_diff.append(label)
    if label == predicted_label:
      accuracy_diff += 1.

accuracy = (accuracy_clear + accuracy_diff) / (n_clear + n_diff)

accuracy_clear /= n_clear
accuracy_diff /= n_diff

  0%|          | 0/1 [00:00<?, ?it/s]

  0%|          | 0/1 [00:00<?, ?it/s]

  0%|          | 0/1 [00:00<?, ?it/s]

  0%|          | 0/1 [00:00<?, ?it/s]

  0%|          | 0/1 [00:00<?, ?it/s]

...

  0%|          | 0/1 [00:00<?, ?it/s]

  0%|          | 0/1 [00:00<?, ?it/s]

  0%|          | 0/1 [00:00<?, ?it/s]

  0%|          | 0/1 [00:00<?, ?it/s]

  0%|          | 0/1 [00:00<?, ?it/s]

In [14]:
print('Accuracy Trainingskorpus:                                                  ', round(accuracy*100, 2), '%,  n =', (n_clear + n_diff))
print('Accuracy Trainingskorpus only on the data that coincides on initial labels:', round(accuracy_clear*100, 2), '%,  n =', n_clear)
print('Accuracy Trainingskorpus only on the data that differs on initial labels:  ', round(accuracy_diff*100, 2), '%,  n = ', n_diff)

Accuracy Trainingskorpus:                                                   69.61 %,  n = 1622
Accuracy Trainingskorpus only on the data that coincides on initial labels: 69.85 %,  n = 1383
Accuracy Trainingskorpus only on the data that differs on initial labels:   68.2 %,  n =  239


In [15]:
# Calculate precision, recall and f1-score for each label

test_df_metrics = precision_recall_fscore_support(testset['kano_labels'], all_predicted_labels, average=None,labels=['B', 'D', 'I', 'P'])

print('Precision B: ', test_df_metrics[0][0])
print('Precision D: ', test_df_metrics[0][1])
print('Precision I: ', test_df_metrics[0][2])
print('Precision P: ', test_df_metrics[0][3])

print('Recall B: ', test_df_metrics[1][0])
print('Recall D: ', test_df_metrics[1][1])
print('Recall I: ', test_df_metrics[1][2])
print('Recall P: ', test_df_metrics[1][3])

print('F1-score B: ', test_df_metrics[2][0])
print('F1-score D: ', test_df_metrics[2][1])
print('F1-score I: ', test_df_metrics[2][2])
print('F1-score P: ', test_df_metrics[2][3])

Precision B:  0.8664688427299704
Precision D:  0.3212669683257919
Precision I:  0.25
Precision P:  0.4689119170984456
Recall B:  0.79491833030853
Recall D:  0.7473684210526316
Recall I:  0.03333333333333333
Recall P:  0.4582278481012658
F1-score B:  0.8291528632276385
F1-score D:  0.44936708860759494
F1-score I:  0.058823529411764705
F1-score P:  0.4635083226632522


In [16]:
# Calculates the phi-coefficient for labels where both researchers agreed vs. where they disagreed

print('MCC for labels where both researchers agreed: ',matthews_corrcoef(true_label_equal, predicted_labels_equal_initial_label))
print('MCC for labels where both researchers disagreed: ',matthews_corrcoef(true_label_diff, predicted_labels_diff_initial_label))

MCC for labels where both researchers agreed:  0.40937050238518985
MCC for labels where both researchers disagreed:  0.4085198339002642


## Combine dataset at hand and 'Trainingskorpus' dataset, then do Train-Test-Split

In [17]:
# Import combined downsampled dataset 
df_combined = pd.read_excel('/content/drive/MyDrive/KANO Modell Studie/Datasets/LabeledDatasets/DATASET_Trainingskorpus_combined.xlsx')
df_combined = df_combined.drop(columns = ['Unnamed: 0'])

# Import without google drive
# df_combined = pd.read_excel('DATASET_Trainingskorpus_combined.xlsx')

# Rename column so that simple transformers can handle it
df_combined = df_combined.rename(columns = {'review': 'text'})
df_combined.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 2972 entries, 0 to 2971
Data columns (total 3 columns):
 #   Column       Non-Null Count  Dtype 
---  ------       --------------  ----- 
 0   text         2972 non-null   object
 1   kano_labels  2972 non-null   object
 2   labels       2972 non-null   int64 
dtypes: int64(1), object(2)
memory usage: 69.8+ KB


In [18]:
# Show the distribution of the labels
print(df_combined['labels'].value_counts())

2    743
3    743
1    743
0    743
Name: labels, dtype: int64


In [19]:
# 10-fold cross validation on the combined dataset

n2 = 10
kf2 = KFold(n_splits=n2, random_state = 42, shuffle = True)

# Lists to store the values of accuracy, f1-score, precision and recall for all 10 folds
resultsAcc2 = []
resultsf12 = []
resultsPrecision2 = []
resultsRecall2 = []

model_args2 = ClassificationArgs(
    num_train_epochs=1, 
    use_multiprocessing=False,
    use_multiprocessing_for_evaluation=False,
    overwrite_output_dir= True
)

# Create a ClassificationModel
model2 = ClassificationModel(
    'albert',
    'albert-base-v2',
    num_labels=4,
    args=model_args,
    #use_cuda=False
) 

for train_index, val_index in kf2.split(df_combined):
  train_df2 = df_combined.iloc[train_index]
  val_df2 = df_combined.iloc[val_index]

  model2.train_model(df_combined)
  result2, model_outputs2, wrong_predictions2 = model2.eval_model(val_df2, f1=f1_multiclass, acc=accuracy_score, recall=recall_multiclass, precision=precision_multiclass)

  print(result2)
  # Add scores to the respective lists
  resultsAcc2.append(result2['acc'])
  resultsf12.append(result2['f1'])
  resultsPrecision2.append(result2['precision'])
  resultsRecall2.append(result2['recall'])

  print("results accuracy",resultsAcc2)
  print(f"Mean-Precision: {sum(resultsAcc2) / len(resultsAcc2)}")
  print('results f1: ', resultsf12)
  print('results precision: ', resultsPrecision2)
  print('results recall: ', resultsRecall2)


Some weights of the model checkpoint at albert-base-v2 were not used when initializing AlbertForSequenceClassification: ['predictions.decoder.weight', 'predictions.dense.weight', 'predictions.bias', 'predictions.decoder.bias', 'predictions.LayerNorm.bias', 'predictions.LayerNorm.weight', 'predictions.dense.bias']
- This IS expected if you are initializing AlbertForSequenceClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing AlbertForSequenceClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of AlbertForSequenceClassification were not initialized from the model checkpoint at albert-base-v2 and are newly initialized: ['classifier.weight', 'classifier.bias']
You sho

Epoch:   0%|          | 0/1 [00:00<?, ?it/s]

Running Epoch 0 of 1:   0%|          | 0/372 [00:00<?, ?it/s]

/usr/local/lib/python3.7/dist-packages/torch/optim/lr_scheduler.py:136: UserWarning: Detected call of `lr_scheduler.step()` before `optimizer.step()`. In PyTorch 1.1.0 and later, you should call them in the opposite order: `optimizer.step()` before `lr_scheduler.step()`.  Failure to do this will result in PyTorch skipping the first value of the learning rate schedule. See more details at https://pytorch.org/docs/stable/optim.html#how-to-adjust-learning-rate
  "https://pytorch.org/docs/stable/optim.html#how-to-adjust-learning-rate", UserWarning)


Running Evaluation:   0%|          | 0/38 [00:00<?, ?it/s]

...

Epoch:   0%|          | 0/1 [00:00<?, ?it/s]

Running Epoch 0 of 1:   0%|          | 0/372 [00:00<?, ?it/s]

/usr/local/lib/python3.7/dist-packages/torch/optim/lr_scheduler.py:136: UserWarning: Detected call of `lr_scheduler.step()` before `optimizer.step()`. In PyTorch 1.1.0 and later, you should call them in the opposite order: `optimizer.step()` before `lr_scheduler.step()`.  Failure to do this will result in PyTorch skipping the first value of the learning rate schedule. See more details at https://pytorch.org/docs/stable/optim.html#how-to-adjust-learning-rate
  "https://pytorch.org/docs/stable/optim.html#how-to-adjust-learning-rate", UserWarning)


Running Evaluation:   0%|          | 0/38 [00:00<?, ?it/s]

{'mcc': 0.8875674205638197, 'f1': array([0.93975904, 0.89855072, 0.91176471, 0.90909091]), 'acc': 0.9158249158249159, 'recall': array([0.93975904, 0.88571429, 0.92537313, 0.90909091]), 'precision': array([0.93975904, 0.91176471, 0.89855072, 0.90909091]), 'eval_loss': 0.2734819587908293}
results accuracy [0.7315436241610739, 0.7013422818791947, 0.797979797979798, 0.7912457912457912, 0.7912457912457912, 0.8417508417508418, 0.8787878787878788, 0.9057239057239057, 0.8956228956228957, 0.9158249158249159]
Mean-Precision: 0.8251067724222085
results f1:  [array([0.8603352 , 0.68478261, 0.86363636, 0.41584158]), array([0.7862069 , 0.72195122, 0.8496732 , 0.27956989]), array([0.88461538, 0.79041916, 0.86896552, 0.61904762]), array([0.84076433, 0.75384615, 0.91139241, 0.6442953 ]), array([0.89922481, 0.7654321 , 0.80597015, 0.72189349]), array([0.90196078, 0.81081081, 0.84931507, 0.80272109]), array([0.90196078, 0.89795918, 0.91970803, 0.80254777]), array([0.92753623, 0.88198758, 0.96052632, 0.85

In [20]:
print("results accuracy",resultsAcc2)
print('results f1: ', resultsf12)
print('results precision: ', resultsPrecision2)
print('results recall: ', resultsRecall2)

results accuracy [0.7315436241610739, 0.7013422818791947, 0.797979797979798, 0.7912457912457912, 0.7912457912457912, 0.8417508417508418, 0.8787878787878788, 0.9057239057239057, 0.8956228956228957, 0.9158249158249159]
results f1:  [array([0.8603352 , 0.68478261, 0.86363636, 0.41584158]), array([0.7862069 , 0.72195122, 0.8496732 , 0.27956989]), array([0.88461538, 0.79041916, 0.86896552, 0.61904762]), array([0.84076433, 0.75384615, 0.91139241, 0.6442953 ]), array([0.89922481, 0.7654321 , 0.80597015, 0.72189349]), array([0.90196078, 0.81081081, 0.84931507, 0.80272109]), array([0.90196078, 0.89795918, 0.91970803, 0.80254777]), array([0.92753623, 0.88198758, 0.96052632, 0.85314685]), array([0.92424242, 0.9202454 , 0.86330935, 0.875     ]), array([0.93975904, 0.89855072, 0.91176471, 0.90909091])]
results precision:  [array([0.83695652, 0.55752212, 0.9047619 , 0.7       ]), array([0.74025974, 0.60655738, 0.87837838, 0.52      ]), array([0.8625    , 0.74157303, 0.88732394, 0.68421053]), array([

In [21]:
# Calculate the average precision, recall and f1-scores of the 10 folds for each label

PrecisionRecallF1Table(resultsPrecision2, resultsRecall2, resultsf12)

B         D         I         P
Average precision  0.875157  0.771229  0.914905  0.747108
Average recall     0.900150  0.871480  0.850669  0.670683
Average F1-Score   0.886661  0.812598  0.880426  0.692315